In [1]:
import os
import hail as hl
import pyspark
import bokeh
from hail.plot import show, output_notebook

tmp_dir = "hdfs://spark-master:9820/"
sc = pyspark.SparkContext()
temp_dir = working_dir = os.path.join(os.environ["HAIL_HOME"], "tmp")
hadoop_config = sc._jsc.hadoopConfiguration()
hadoop_config.set("fs.s3a.access.key", "8YY584J59H7Q6AVKHSU8")
hadoop_config.set("fs.s3a.secret.key", "P8vePa7JUvxKXX2me9ti1cGujgYWMoimAwx4mMlM")
hadoop_config.set("fs.gs.impl", "com.google.cloud.hadoop.fs.gcs.GoogleHadoopFileSystem")
hadoop_config.set("fs.AbstractFileSystem.gs.impl", "com.google.cloud.hadoop.fs.gcs.GoogleHadoopFS")
hl.init(sc=sc, tmp_dir=tmp_dir, default_reference='GRCh38')
output_notebook()

/opt/sanger.ac.uk/hgi/anaconda3/lib/python3.7/site-packages/hail/context.py:71: UserWarning: pip-installed Hail requires additional configuration options in Spark referring
  to the path to the Hail Python module directory HAIL_DIR,
  e.g. /path/to/python/site-packages/hail:
    spark.jars=HAIL_DIR/hail-all-spark.jar
    spark.driver.extraClassPath=HAIL_DIR/hail-all-spark.jar
    spark.executor.extraClassPath=./hail-all-spark.jar
  'pip-installed Hail requires additional configuration options in Spark referring\n'
Running on Apache Spark version 2.4.3
SparkUI available at http://spark-master:4040
Welcome to
     __  __     <>__
    / /_/ /__  __/ /
   / __  / _ `/ / /
  /_/ /_/\_,_/_/_/   version 0.2.31-6060f9c971cc
LOGGING: writing to /opt/sanger.ac.uk/hgi/hail/tmp/scripts/sanger_gnomad_hail_qc/hail-20200714-1635-0.2.31-6060f9c971cc.log


Loading BokehJS ...

In [2]:
ht=hl.read_table(f"{temp_dir}/ddd-elgh-ukbb/pc_project_our_data.ht")
project_mt = hl.read_matrix_table(
        f"{temp_dir}/ddd-elgh-ukbb/relatedness_ancestry/ddd-elgh-ukbb/chr1_chr20_XY_ldpruned.mt")

mt=project_mt.annotate_cols(scores=ht[project_mt.s].scores)

In [5]:
mt.scores.count()

AttributeError: 'ArrayNumericExpression' object has no attribute 'count'

In [3]:
mt.describe()

----------------------------------------
Global fields:
    None
----------------------------------------
Column fields:
    's': str
    'cohort': str
    'f_stat': float64
    'is_female': bool
    'sex': str
    'data_type': str
    'scores': array<float64>
----------------------------------------
Row fields:
    'locus': locus<GRCh38>
    'alleles': array<str>
    'rsid': str
    'qual': float64
    'filters': set<str>
    'info': struct {
        AC: array<int32>, 
        AF: array<float64>, 
        AN: int32, 
        AS_BaseQRankSum: array<float64>, 
        AS_FS: array<float64>, 
        AS_InbreedingCoeff: array<float64>, 
        AS_MQ: array<float64>, 
        AS_MQRankSum: array<float64>, 
        AS_QD: array<float64>, 
        AS_ReadPosRankSum: array<float64>, 
        AS_SOR: array<float64>, 
        BaseQRankSum: float64, 
        DB: bool, 
        DP: int32, 
        DS: bool, 
        END: int32, 
        ExcessHet: float64, 
        FS: float64, 
        Inbreed

In [4]:
p1=hl.plot.scatter(mt.scores[0], mt.scores[1], xlabel="PC1", ylabel="PC2", label=mt.cohort)
p2=hl.plot.scatter(mt.scores[0], mt.scores[2], xlabel="PC1", ylabel="PC3", label=mt.cohort)
p3=hl.plot.scatter(mt.scores[1], mt.scores[3], xlabel="PC2", ylabel="PC4", label=mt.cohort)
p4=hl.plot.scatter(mt.scores[4], mt.scores[9], xlabel="PC5", ylabel="PC10", label=mt.cohort)
p5=hl.plot.scatter(mt.scores[6], mt.scores[8], xlabel="PC7", ylabel="PC9", label=mt.cohort)


show(bokeh.layouts.gridplot([[p1],[p2],[p3],[p4],[p5]]))